In [1]:
import os
from tqdm.notebook import tqdm
import polars as pl
import json
import numpy as np
import matplotlib.pyplot as plt
import matplotlib.gridspec as gridspec
import datetime


In [2]:
# Existing dataset dir
data_dir = './data/'

# Existing plots dir
plots_dir = data_dir+'/plots/'
os.makedirs(data_dir, exist_ok=True)
os.makedirs(plots_dir, exist_ok=True)


In [3]:
file_name_1 = "./data/swaps-base-Uniswap-v3-WETH-USDC.paraquet"
file_name_2 = "./data/swaps-optimism-Uniswap-v3-WETH-USDC.paraquet"
contract_name1 = 'base'

# Load the parquet file
swaps_df1 = pl.scan_parquet(file_name_1).collect(streaming=True)
swaps_df2 = pl.scan_parquet(file_name_2).collect(streaming=True)


#swaps_df1.shape[0]


In [4]:
print(swaps_df1.columns)

['transaction_hash', 'transaction_index', 'log_index', 'block_number', 'block_timestamp', 'amount_ETH', 'amount_USD', 'sqrtPriceX96', 'tick', 'liquidity', 'effective_price', 'spot_price', 'reserve_ETH', 'reserve_USD', 'CEX_price']


In [5]:
start_date = pl.datetime(2024,4,26)
end_date = pl.datetime(2024,4,28)

swaps_df1 = swaps_df1.filter(
    (pl.col('block_timestamp') < end_date) & (pl.col('block_timestamp') > start_date)
    )

swaps_df2 = swaps_df2.filter(
    (pl.col('block_timestamp') < end_date) & (pl.col('block_timestamp') > start_date)
    )

In [6]:
swaps_df1.shape[0]

61909

In [10]:
swaps_df2.shape[0]

21555

In [7]:
import plotly.graph_objects as go
#from utils_plot import *
from kaleido import *

colors = {'red': '#ee443a', 'blue': '#42bbf1', 'dark_blue': '#1a4fec',
          'green': '#50be61', 'grey': '#b7b7b7', 'orange': '#f28222', 'purple': '#6e18ee', 'brown': '#a65628', 'pink': '#ef4793',
          'yellow': '#f8c94c', 'black': '#000000', 'white': '#ffffff', 'light_blue': '#a6cee3', 'light_green': '#b2df8a',
          'light_grey': '#999999', 'light_orange': '#fdbf6f', 'light_purple': '#cab2d6', 'light_brown': '#ffff99', 'light_pink': '#1f78b4',
          'light_yellow': '#fb9a99', 'light_black': '#e31a1c', 'light_white': '#33a02c', 'gold': '#ff7f00', 'silver': '#b2df8a'}

layout = go.Layout(
    margin=go.layout.Margin(
        l=10,  # left margin
        r=10,  # right margin
        b=10,  # bottom margin
        t=10  # top margin
    ),
    template='simple_white',
    xaxis=dict(minor_ticks="inside", showgrid=True, griddash='dash',
               minor_griddash="dot"),
    yaxis=dict(minor_ticks="inside", showgrid=True, griddash='dash',
               minor_griddash="dot"),
    #font=dict(size=18, family='Clear Sans',
    #          color='black'),

)

settings = {
    'AddLiquidity': {'color': colors['blue'], 'style': None, 'width': 4.5},
    'RemoveLiquidity': {'color': colors['red'], 'style': 'dash', 'width': 4},
    'RemoveLiquidityOne': {'color': colors['green'], 'style': 'dot', 'width': 3.5},
    'RemoveLiquidityImbalance': {'color': colors['brown'], 'style': 'dashdot', 'width': 3},
}



In [8]:

fig = go.Figure(layout=layout)
fig.update_layout(width=600, height=300)

fig.add_trace(go.Scatter(x=swaps_df1['block_timestamp'],
                            y=swaps_df1['spot_price'],
                            mode='lines',
                            name = 'AMM 1 ETH Price'))

fig.add_trace(go.Scatter(x=swaps_df2['block_timestamp'],
                            y=swaps_df2['spot_price'],
                            mode='lines',
                            name = 'AMM 2 ETH Price'))

fig.update_layout(  yaxis_title='Daily close price (USD)', showlegend=True,
                    legend=dict(xanchor='center', x=0.5, y=1.10, orientation='h'),)

fig.write_image(f"./plots/{contract_name1}.pdf")

fig.show()



In [13]:
from dtaidistance import dtw
from dtaidistance import dtw_visualisation as dtwvis
import numpy as np
s1 = np.array([0., 0, 1, 2, 1, 0, 1, 0, 0, 2, 1, 0, 0])
s2 = np.array([0., 1, 2, 3, 1, 0, 0, 0, 2, 1, 0, 0, 0])
path = dtw.warping_path(s1, s2)
dtwvis.plot_warping(s1, s2, path, filename="warp.png")

(None, None)

In [17]:
s1 = np.array(swaps_df1['spot_price'])
s2 = np.array(swaps_df2['spot_price'])

In [18]:
path = dtw.warping_path(s1, s2)
dtwvis.plot_warping(s1, s2, path, filename="warp.png")

KeyboardInterrupt: 

In [10]:
import numpy as np

# We define two sequences x, y as numpy array
# where y is actually a sub-sequence from x
x = np.array([2, 0, 1, 1, 2, 4, 2, 1, 2, 0]).reshape(-1, 1)
y = np.array([1, 1, 2, 4, 2, 1, 2, 0]).reshape(-1, 1)

from dtw import dtw

manhattan_distance = lambda x, y: np.abs(x - y)

d, cost_matrix, acc_cost_matrix, path = dtw(x, y, dist=manhattan_distance)

print(d)
#>>> 2.0 # Only the cost for the insertions is kept

# You can also visualise the accumulated cost and the shortest path
import matplotlib.pyplot as plt

plt.imshow(acc_cost_matrix.T, origin='lower', cmap='gray', interpolation='nearest')
plt.plot(path[0], path[1], 'w')
plt.show()

2.0


In [ ]:

# We define two sequences x, y as numpy array
# where y is actually a sub-sequence from x
x = np.array([2, 0, 1, 1, 2, 4, 2, 1, 2, 0]).reshape(-1, 1)
y = np.array([1, 1, 2, 4, 2, 1, 2, 0]).reshape(-1, 1)


manhattan_distance = lambda x, y: np.abs(x - y)

d, cost_matrix, acc_cost_matrix, path = dtw(x, y, dist=manhattan_distance)

print(d)
#>>> 2.0 # Only the cost for the insertions is kept

# You can also visualise the accumulated cost and the shortest path
import matplotlib.pyplot as plt

plt.imshow(acc_cost_matrix.T, origin='lower', cmap='gray', interpolation='nearest')
plt.plot(path[0], path[1], 'w')
plt.show()

In [11]:
x = np.array(swaps_df1['spot_price'])
y = np.array(swaps_df2['spot_price'])

manhattan_distance = lambda x, y: np.abs(x - y)

d, cost_matrix, acc_cost_matrix, path = dtw(x, y, dist=manhattan_distance)

print(d)
#>>> 2.0 # Only the cost for the insertions is kept

# You can also visualise the accumulated cost and the shortest path
import matplotlib.pyplot as plt

plt.imshow(acc_cost_matrix.T, origin='lower', cmap='gray', interpolation='nearest')
plt.plot(path[0], path[1], 'w')
plt.show()

KeyboardInterrupt: 